-sandbox

<div style="text-align: center; line-height: 0; padding-top: 9px;">
  <img src="https://databricks.com/wp-content/uploads/2018/03/db-academy-rgb-1200px.png" alt="Databricks Learning" style="width: 600px">
</div>

# Exercise #3 - Create Fact & Dim Tables

Now that the three years of orders are combined into a single dataset, we can begin the processes of transforming the data.

In the one record, there are actually four sub-datasets:
* The order itself which is the aggregator of the other three datasets.
* The line items of each order which includes the price and quantity of each specific item.
* The sales rep placing the order.
* The customer placing the order - for the sake of simplicity, we will **not** break this dataset out and leave it as part of the order.

What we want to do next, is to extract all that data into their respective datasets (except the customer data). 

In other words, we want to normalize the data, in this case, to reduce data duplication.

This exercise is broken up into 5 steps:
* Exercise 3.A - Create & Use Database
* Exercise 3.B - Load & Cache Batch Orders
* Exercise 3.C - Extract Sales Reps
* Exercise 3.D - Extract Orders
* Exercise 3.E - Extract Line Items

<h2><img src="https://files.training.databricks.com/images/105/logo_spark_tiny.png"> Setup Exercise #3</h2>

To get started, we first need to configure your Registration ID and then run the setup notebook.

### Setup - Registration ID

In the next command, please update the variable **`registration_id`** with the Registration ID you received when you signed up for this project.

For more information, see [Registration ID]($./Registration ID)

In [0]:
registration_id = "3203488"

### Setup - Run the exercise setup

Run the following cell to setup this exercise, declaring exercise-specific variables and functions.

In [0]:
%run ./_includes/Setup-Exercise-03

The following variables and functions have been defined for you. Please refer to them in the following instructions. Variable/Function 
 Description username 
 andrew.barry@infinitive.com 
   
 This is the email address that you signed into Databricks with working_dir 
 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone 
   
 This is the directory in which all work should be conducted user_db 
 dbacademy_andrew_barry_infinitive_com_db 
   
 The name of the database you will use for this project. batch_source_path 
 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/batch_orders_dirty.delta 
   
 The location of the combined, raw, batch of orders. orders_table 
 orders 
   
 The name of the orders table. line_items_table 
 line_items 
   
 The name of the line items table. sales_reps_table 
 sales_reps 
   
 The name of the sales reps table. batch_temp_view 
 batched_orders 
   
 The name of the temp view used in this exercise reality_check_03_a() 
 A utility function for validating Exercise #3.A reality_check_03_b() 
 A utility function for validating Exercise #3.B reality_check_03_c() 
 A utility function for validating Exercise #3.C reality_check_03_d() 
 A utility function for validating Exercise #3.D reality_check_03_e() 
 A utility function for validating Exercise #3.E reality_check_03_final() 
 A utility function for validating the entire exercise

<h2><img src="https://files.training.databricks.com/images/105/logo_spark_tiny.png"> Exercise #3.A - Create &amp; Use Database</h2>

By using a specific database, we can avoid contention to commonly named tables that may be in use by other users of the workspace.

**In this step you will need to:**
* Create the database identified by the variable **`user_db`**
* Use the database identified by the variable **`user_db`** so that any tables created in this notebook are **NOT** added to the **`default`** database

**Special Notes**
* Do not hard-code the database name - in some scenarios this will result in validation errors.
* For assistence with the SQL command to create a database, see <a href="https://docs.databricks.com/spark/latest/spark-sql/language-manual/sql-ref-syntax-ddl-create-database.html" target="_blank">CREATE DATABASE</a> on the Databricks docs website.
* For assistence with the SQL command to use a database, see <a href="https://docs.databricks.com/spark/latest/spark-sql/language-manual/sql-ref-syntax-ddl-usedb.html" target="_blank">USE DATABASE</a> on the Databricks docs website.

### Implement Exercise #3.A

Implement your solution in the following cell:

In [0]:
create_query = "CREATE DATABASE {};".format(user_db)
use_query = "USE {};".format(user_db)

sqlContext.sql(create_query)
sqlContext.sql(use_query)

Out[15]: DataFrame[]

### Reality Check #3.A
Run the following command to ensure that you are on track:

In [0]:
reality_check_03_a()

Points Test Result 
 
 1 
 
 Using DBR 7.3 LTS, with 8 cores
 
 
 
 
 1 
 
 Valid Registration ID
 
 
 
 
 1 
 
 The current database is dbacademy_andrew_barry_infinitive_com_db
 
 
 
 Score: 3

<h2><img src="https://files.training.databricks.com/images/105/logo_spark_tiny.png"> Exercise #3.B - Load &amp; Cache Batch Orders</h2>

Next, we need to load the batch orders from the previous exercise and then cache them in preparation to transform the data later in this exercise.

**In this step you will need to:**
* Load the delta dataset we created in the previous exercise, identified by the variable **`batch_source_path`**.
* Using that same dataset, create a temporary view identified by the variable **`batch_temp_view`**.
* Cache the temporary view.

### Implement Exercise #3.B

Implement your solution in the following cell:

In [0]:
delta_table = spark.read.format("delta").load(batch_source_path)

delta_table.createOrReplaceTempView(batch_temp_view)

sqlContext.cacheTable(batch_temp_view)

### Reality Check #3.B
Run the following command to ensure that you are on track:

In [0]:
reality_check_03_b()

Points Test Result 
 
 1 
 
 The current database is dbacademy_andrew_barry_infinitive_com_db
 
 
 
 
 1 
 
 The table batched_orders exists
 
 
 
 
 1 
 
 The table batched_orders is a temp view
 
 
 
 
 1 
 
 The table batched_orders is cached
 
 
 
 
 1 
 
 Expected 1,175,870 records
 
 
 
 Score: 5

<h2><img src="https://files.training.databricks.com/images/105/logo_spark_tiny.png"> Exercise #3.C - Extract Sales Reps</h2>

Our batched orders from Exercise #2 contains thousands of orders and with every order, is the name, SSN, address and other information on the sales rep making the order.

We can use this data to create a table of just our sales reps.

If you consider that we have only ~100 sales reps, but thousands of orders, we are going to have a lot of duplicate data in this space.

Also unique to this set of data, is the fact that social security numbers were not always sanitized meaning sometime they were formatted with hyphens and in other cases they were not - this is something we will have to address here.

**In this step you will need to:**
* Load the table **`batched_orders`** (identified by the variable **`batch_temp_view`**)
* The SSN numbers have errors in them that we want to track - add the **`boolean`** column **`_error_ssn_format`** - for any case where **`sales_rep_ssn`** has a hypen in it, set this value to **`true`** otherwise **`false`**
* Convert various columns from their string representation to the specified type:
  * The column **`sales_rep_ssn`** should be represented as a **`Long`** (Note: You will have to first clean the column by removing extreneous hyphens in some records)
  * The column **`sales_rep_zip`** should be represented as an **`Integer`**
* Remove the columns not directly related to the sales-rep record:
  * Unrelated ID columns: **`submitted_at`**, **`order_id`**, **`customer_id`**
  * Shipping address columns: **`shipping_address_attention`**, **`shipping_address_address`**, **`shipping_address_city`**, **`shipping_address_state`**, **`shipping_address_zip`**
  * Product columns: **`product_id`**, **`product_quantity`**, **`product_sold_price`**
* Because there is one record per product ordered (many products per order), not to mention one sales rep placing many orders (many orders per sales rep), there will be duplicate records for our sales reps. Remove all duplicate records, making sure to exclude **`ingest_file_name`** and **`ingested_at`** from the evaluation of duplicate records
* Load the dataset to the managed delta table **`sales_rep_scd`** (identified by the variable **`sales_reps_table`**)

**Additional Requirements:**<br/>
The schema for the **`sales_rep_scd`** table must be:
* **`sales_rep_id`**:**`string`**
* **`sales_rep_ssn`**:**`long`**
* **`sales_rep_first_name`**:**`string`**
* **`sales_rep_last_name`**:**`string`**
* **`sales_rep_address`**:**`string`**
* **`sales_rep_city`**:**`string`**
* **`sales_rep_state`**:**`string`**
* **`sales_rep_zip`**:**`integer`**
* **`ingest_file_name`**:**`string`**
* **`ingested_at`**:**`timestamp`**
* **`_error_ssn_format`**:**`boolean`**

### Implement Exercise #3.C

Implement your solution in the following cell:

In [0]:
from pyspark.sql.functions import *

df = spark.sql("select * from batched_orders")
df = df.drop("submitted_at", "order_id", "customer_id", "shipping_address_attention", "shipping_address_address", "shipping_address_city", "shipping_address_state", "shipping_address_zip", "product_id", "product_quantity", "product_sold_price")

display(df.filter(col("ingested_at").isNull()))

sales_rep_id sales_rep_ssn sales_rep_first_name sales_rep_last_name sales_rep_address sales_rep_city sales_rep_state sales_rep_zip ingest_file_name ingested_at

In [0]:
def ssn_error(x):
  if x is None:
    return False
  elif "-" in x:
    return True
  else:
    return False
    
    
ssn_udf = udf(ssn_error)

df = df.withColumn("_error_ssn_format", ssn_udf(df["sales_rep_ssn"]))

display(df)

sales_rep_id sales_rep_ssn sales_rep_first_name sales_rep_last_name sales_rep_address sales_rep_city sales_rep_state sales_rep_zip ingest_file_name ingested_at _error_ssn_format c58e0ea1-93ad-4ea2-b45b-32d46ccb941d 575751925 Mackenzie Burgess PO Box 79 Scottsdale AZ 85333 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false c58e0ea1-93ad-4ea2-b45b-32d46ccb941d 575751925 Mackenzie Burgess PO Box 79 Scottsdale AZ 85333 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false c58e0ea1-93ad-4ea2-b45b-32d46ccb941d 575751925 Mackenzie Burgess PO Box 79 Scottsdale AZ 85333 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false c58e0ea1-93ad-4ea2-b45b-32d46ccb941d 575751925 Mackenzie Burgess PO Box 79 Scottsdale AZ 85333 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false 830da307-c958-46d1-862b-ed79c7753f85 888-83-5002 Melvin Obrien 58 Delk Drive S Honolulu HI 96732 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 true 830da307-c958-46d1-862b-ed79c7753f85 888-83-5002 Melvin Obrien 58 Delk Drive S Honolulu HI 96732 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 true 59c25563-37ee-4cb3-bce0-51d3bc2f1068 572683011 Esteban Cooley 266 Knoll Place E Waterbury CT 06853 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false 59c25563-37ee-4cb3-bce0-51d3bc2f1068 572683011 Esteban Cooley 266 Knoll Place E Waterbury CT 06853 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false 59c25563-37ee-4cb3-bce0-51d3bc2f1068 572683011 Esteban Cooley 266 Knoll Place E Waterbury CT 06853 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false 59c25563-37ee-4cb3-bce0-51d3bc2f1068 572683011 Esteban Cooley 266 Knoll Place E Waterbury CT 06853 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false 59c25563-37ee-4cb3-bce0-51d3bc2f1068 572683011 Esteban Cooley 266 Knoll Place E Waterbury CT 06853 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false b51c9e0d-a515-4fc0-a7a1-a50b3fe11213 757901809 Davina Arnold 274 Emporia Place Vacaville CA 95932 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false b51c9e0d-a515-4fc0-a7a1-a50b3fe11213 757901809 Davina Arnold 274 Emporia Place Vacaville CA 95932 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false b51c9e0d-a515-4fc0-a7a1-a50b3fe11213 757901809 Davina Arnold 274 Emporia Place Vacaville CA 95932 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false b51c9e0d-a515-4fc0-a7a1-a50b3fe11213 757901809 Davina Arnold 274 Emporia Place Vacaville CA 95932 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false 9164bbb1-df84-498a-885e-68fb6f743847 211582548 Andrea Yates PO Box 241 Denton TX 77034 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 false 9164bbb1-df84-498a-8

In [0]:
df = (df.withColumn("sales_rep_ssn", col("sales_rep_ssn").astype("long")).withColumn("sales_rep_zip", col("sales_rep_zip").astype("int"))
      .withColumn("_error_ssn_format", col("_error_ssn_format").astype("boolean")).dropDuplicates(["sales_rep_id", "sales_rep_ssn", "sales_rep_first_name", "sales_rep_last_name", "sales_rep_address", "sales_rep_city", "sales_rep_state", "sales_rep_zip"]))

In [0]:
df.printSchema()

root
-- sales_rep_id: string (nullable = true)
-- sales_rep_ssn: long (nullable = true)
-- sales_rep_first_name: string (nullable = true)
-- sales_rep_last_name: string (nullable = true)
-- sales_rep_address: string (nullable = true)
-- sales_rep_city: string (nullable = true)
-- sales_rep_state: string (nullable = true)
-- sales_rep_zip: integer (nullable = true)
-- ingest_file_name: string (nullable = true)
-- ingested_at: timestamp (nullable = true)
-- _error_ssn_format: boolean (nullable = true)

In [0]:
df.write.format("delta").mode("overwrite").saveAsTable(sales_reps_table)

### Reality Check #3.C
Run the following command to ensure that you are on track:

In [0]:
reality_check_03_c()

Points Test Result 
 
 1 
 
 The current database is dbacademy_andrew_barry_infinitive_com_db
 
 
 
 
 1 
 
 The table sales_reps exists
 
 
 
 
 1 
 
 The table sales_reps is a managed table
 
 
 
 
 1 
 
 Using the Delta file format
 
 
 
 
 1 
 
 Schema is valid
 
 
 
 
 1 
 
 Expected 93 records
 
 
 
 
 1 
 
 Expected _error_ssn_format record count to be 17
 
 
 
 Score: 7

<h2><img src="https://files.training.databricks.com/images/105/logo_spark_tiny.png"> Exercise #3.D - Extract Orders</h2>

Our batched orders from Exercise 02 contains one line per product meaning there are multiple records per order.

The goal of this step is to extract just the order details (excluding the sales rep and line items)

**In this step you will need to:**
* Load the table **`batched_orders`** (identified by the variable **`batch_temp_view`**)
* Convert various columns from their string representation to the specified type:
  * The column **`submitted_at`** is a "unix epoch" (number of seconds since 1970-01-01 00:00:00 UTC) and should be represented as a **`Timestamp`**
  * The column **`shipping_address_zip`** should be represented as an **`Integer`**
* Remove the columns not directly related to the order record:
  * Sales reps columns: **`sales_rep_ssn`**, **`sales_rep_first_name`**, **`sales_rep_last_name`**, **`sales_rep_address`**, **`sales_rep_city`**, **`sales_rep_state`**, **`sales_rep_zip`**
  * Product columns: **`product_id`**, **`product_quantity`**, **`product_sold_price`**
* Because there is one record per product ordered (many products per order), there will be duplicate records for each order. Remove all duplicate records, making sure to exclude **`ingest_file_name`** and **`ingested_at`** from the evaluation of duplicate records
* Add the column **`submitted_yyyy_mm`** which is a **`string`** derived from **`submitted_at`** and is formatted as "**yyyy-MM**".
* Load the dataset to the managed delta table **`orders`** (identified by the variable **`orders_table`**)
  * In thise case, the data must also be partitioned by **`submitted_yyyy_mm`**

**Additional Requirements:**
* The schema for the **`orders`** table must be:
  * **`submitted_at:timestamp`**
  * **`submitted_yyyy_mm`** using the format "**yyyy-MM**"
  * **`order_id:string`**
  * **`customer_id:string`**
  * **`sales_rep_id:string`**
  * **`shipping_address_attention:string`**
  * **`shipping_address_address:string`**
  * **`shipping_address_city:string`**
  * **`shipping_address_state:string`**
  * **`shipping_address_zip:integer`**
  * **`ingest_file_name:string`**
  * **`ingested_at:timestamp`**

### Implement Exercise #3.D

Implement your solution in the following cell:

In [0]:
df2 = spark.sql("select * from batched_orders")
display(df2)

submitted_at order_id customer_id sales_rep_id sales_rep_ssn sales_rep_first_name sales_rep_last_name sales_rep_address sales_rep_city sales_rep_state sales_rep_zip shipping_address_attention shipping_address_address shipping_address_city shipping_address_state shipping_address_zip product_id product_quantity product_sold_price ingest_file_name ingested_at 1527836400 c76bccfd-ff08-4aea-8f4e-044f49335d80 96790325-06f1-4551-9aae-4b2044ba3584 c58e0ea1-93ad-4ea2-b45b-32d46ccb941d 575751925 Mackenzie Burgess PO Box 79 Scottsdale AZ 85333 Camryn Howard 10 N Valparaiso Street Minneapolis MN 56381 7a41323a-560f-4e34-aba6-995e2325f95e 500 101.23 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 1527836400 c76bccfd-ff08-4aea-8f4e-044f49335d80 96790325-06f1-4551-9aae-4b2044ba3584 c58e0ea1-93ad-4ea2-b45b-32d46ccb941d 575751925 Mackenzie Burgess PO Box 79 Scottsdale AZ 85333 Camryn Howard 10 N Valparaiso Street Minneapolis MN 56381 8d809e13-fdc5-4d15-9271-953750f6d592 700 112.48 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 1527836400 c76bccfd-ff08-4aea-8f4e-044f49335d80 96790325-06f1-4551-9aae-4b2044ba3584 c58e0ea1-93ad-4ea2-b45b-32d46ccb941d 575751925 Mackenzie Burgess PO Box 79 Scottsdale AZ 85333 Camryn Howard 10 N Valparaiso Street Minneapolis MN 56381 95cbadca-cf90-4b8a-a134-2976f6ba6df8 1000 106.85 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 1527836400 c76bccfd-ff08-4aea-8f4e-044f49335d80 96790325-06f1-4551-9aae-4b2044ba3584 c58e0ea1-93ad-4ea2-b45b-32d46ccb941d 575751925 Mackenzie Burgess PO Box 79 Scottsdale AZ 85333 Camryn Howard 10 N Valparaiso Street Minneapolis MN 56381 a8fbcfea-4352-4c5a-af8b-c8623258b4f8 1000 111.35 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 1531483200 c76bdbf6-6564-45e5-9393-870c6dec4b27 b01314da-42ca-420a-b1f3-c7ed50094d14 830da307-c958-46d1-862b-ed79c7753f85 888-83-5002 Melvin Obrien 58 Delk Drive S Honolulu HI 96732 Paityn Dalton 613 E Sweetgum Street Provo UT 84189 7b547a10-e804-48e1-ad90-1f946cee659c 900 100.09 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 1531483200 c76bdbf6-6564-45e5-9393-870c6dec4b27 b01314da-42ca-420a-b1f3-c7ed50094d14 830da307-c958-46d1-862b-ed79c7753f85 888-83-5002 Melvin Obrien 58 Delk Drive S Honolulu HI 96732 Paityn Dalton 613 E Sweetgum Street Provo UT 84189 bc93ed89-bb15-4e46-a110-a5878e46ccf6 900 90.08 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 1527742800 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 5dea97b0-ad78-4da0-bd54-563a1a851193 59c25563-37ee-4cb3-bce0-51d3bc2f1068 572683011 Esteban Cooley 266 Knoll Place E Waterbury CT 06853 Rosalyn Blake 900 Azalea Drive Savannah GA 31750 668b2c1f-d76e-4bf0-82bb-c7d5776524a4 500 108.66 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 1527742800 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 5dea97b0-ad78-4da0-bd54-563a1a851193 59c25563-37ee-4cb3-bce0-51d3bc2f1068 572683011 Esteban Cooley 266 Knoll Place E Waterbury CT 06853 Rosalyn Blake 900 Azalea Drive Savannah GA 31750 7a41323a-560f-4e34-aba6-995e2325f95e 800 97.80 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 1527742800 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 5dea97b0-ad78-4da0-bd54-563a1a851193 59c25563-37ee-4cb3-bce0-51d3bc2f1068 572683011 Esteban Cooley 266 Knoll Place E Waterbury CT 06853 Rosalyn Blake 900 Azalea Drive Savannah GA 31750 8d809e13-fdc5-4d15-9271-953750f6d592 600 108.66 dbfs:/user/a

In [0]:
df2 = (df2.withColumn("submitted_at", from_unixtime(col("submitted_at")).astype("timestamp")).withColumn("shipping_address_zip", col("shipping_address_zip").astype("int"))
  .drop("sales_rep_ssn", "sales_rep_first_name", "sales_rep_last_name", "sales_rep_address", "sales_rep_city", "sales_rep_state", "sales_rep_zip", "product_id", "product_quantity", "product_sold_price"))

In [0]:
display(df2)

submitted_at order_id customer_id sales_rep_id shipping_address_attention shipping_address_address shipping_address_city shipping_address_state shipping_address_zip ingest_file_name ingested_at 2018-06-01T07:00:00.000+0000 c76bccfd-ff08-4aea-8f4e-044f49335d80 96790325-06f1-4551-9aae-4b2044ba3584 c58e0ea1-93ad-4ea2-b45b-32d46ccb941d Camryn Howard 10 N Valparaiso Street Minneapolis MN 56381 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-06-01T07:00:00.000+0000 c76bccfd-ff08-4aea-8f4e-044f49335d80 96790325-06f1-4551-9aae-4b2044ba3584 c58e0ea1-93ad-4ea2-b45b-32d46ccb941d Camryn Howard 10 N Valparaiso Street Minneapolis MN 56381 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-06-01T07:00:00.000+0000 c76bccfd-ff08-4aea-8f4e-044f49335d80 96790325-06f1-4551-9aae-4b2044ba3584 c58e0ea1-93ad-4ea2-b45b-32d46ccb941d Camryn Howard 10 N Valparaiso Street Minneapolis MN 56381 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-06-01T07:00:00.000+0000 c76bccfd-ff08-4aea-8f4e-044f49335d80 96790325-06f1-4551-9aae-4b2044ba3584 c58e0ea1-93ad-4ea2-b45b-32d46ccb941d Camryn Howard 10 N Valparaiso Street Minneapolis MN 56381 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-07-13T12:00:00.000+0000 c76bdbf6-6564-45e5-9393-870c6dec4b27 b01314da-42ca-420a-b1f3-c7ed50094d14 830da307-c958-46d1-862b-ed79c7753f85 Paityn Dalton 613 E Sweetgum Street Provo UT 84189 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-07-13T12:00:00.000+0000 c76bdbf6-6564-45e5-9393-870c6dec4b27 b01314da-42ca-420a-b1f3-c7ed50094d14 830da307-c958-46d1-862b-ed79c7753f85 Paityn Dalton 613 E Sweetgum Street Provo UT 84189 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-05-31T05:00:00.000+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 5dea97b0-ad78-4da0-bd54-563a1a851193 59c25563-37ee-4cb3-bce0-51d3bc2f1068 Rosalyn Blake 900 Azalea Drive Savannah GA 31750 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-05-31T05:00:00.000+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 5dea97b0-ad78-4da0-bd54-563a1a851193 59c25563-37ee-4cb3-bce0-51d3bc2f1068 Rosalyn Blake 900 Azalea Drive Savannah GA 31750 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-05-31T05:00:00.000+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 5dea97b0-ad78-4da0-bd54-563a1a851193 59c25563-37ee-4cb3-bce0-51d3bc2f1068 Rosalyn Blake 900 Azalea Drive Savannah GA 31750 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-05-31T05:00:00.000+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 5dea97b0-ad78-4da0-bd54-563a1a851193 59c25563-37ee-4cb3-bce0-51d3bc2f1068 Rosalyn Blake 900 Azalea Drive Savannah GA 31750 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-05-31T05:00:00.000+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 5dea97b0-ad78-4da0-bd54-563a1a851193 59c25563-37ee-4cb3-bce0-51d3bc2f1068 Rosalyn Blake 900 Azalea Drive Savannah GA 31750 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-04-18T08:00:00.000+0000 c770d7d7-ebed-43ff-9813-6382b02a8500 3676f574-0b7b-47b1-9032-686c5fa9b562 b51c9e0d-a515-4fc0-a7a1-a50b3fe11213 Aleah Mcdowell 518 N Keystone Court Roseville CA 93240 dbfs:/u

In [0]:
df2 = df2.dropDuplicates(["submitted_at", "order_id", "customer_id", "sales_rep_id", "shipping_address_attention", "shipping_address_address", "shipping_address_city", "shipping_address_state", "shipping_address_zip"])

In [0]:
display(df2.filter(col("ingested_at").isNull()))

submitted_at order_id customer_id sales_rep_id shipping_address_attention shipping_address_address shipping_address_city shipping_address_state shipping_address_zip ingest_file_name ingested_at

In [0]:
from datetime import datetime

def parse_month(x):
  if x is None:
    return None
  else:
    string = x.strftime("%Y-%m")
    return string
  
month_udf = udf(parse_month)
  
df2 = df2.withColumn("submitted_yyyy_mm", month_udf(col("submitted_at")))

In [0]:
display(df2)

submitted_at order_id customer_id sales_rep_id shipping_address_attention shipping_address_address shipping_address_city shipping_address_state shipping_address_zip ingest_file_name ingested_at submitted_yyyy_mm 2017-07-22T13:00:00.000+0000 0003ecad-6827-4ad3-a80d-fbeb1569d2cb 00b54fb1-a8cf-471d-869b-e368a77a5f2f 4a888d8f-afe0-4ba3-b76d-08f25e0dea27 Waverly Estrada 898 Dalecroft Trail W Rancho Cucamonga CA 93774 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2017.txt 2021-09-17T22:34:20.902+0000 2017-07 2017-05-01T17:00:00.000+0000 0008c4b7-3eab-4805-95f3-497c7e11f27a fb514f0e-8535-4cb6-acdb-424c732f0062 af0f3842-846d-4e3f-9763-049978937827 Davis Garner 109 Wales Plaza E Roseville CA 92280 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2017.txt 2021-09-17T22:34:20.902+0000 2017-05 2019-01-28T06:00:00.000+0000 000a765a-38fe-4e19-93e6-2dc552f84eef f07e0e28-803a-492d-b6b3-e5382044e1ae 4898862a-68d3-43e5-8627-caf6933bdaec Tanner Gross 456 Ravenel Court Gainesville FL 32936 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2019.csv 2021-09-17T22:40:33.749+0000 2019-01 2017-07-20T17:00:00.000+0000 0015677d-b05b-49c7-a9b0-d53abd852b49 80592e9d-b11e-487f-9565-0b7f9af10f9c 95a919b4-5c80-4242-bf0e-66e3443ee504 Saoirse Lee 395 Rockville Place Lewisville TX 78629 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2017.txt 2021-09-17T22:34:20.902+0000 2017-07 2018-04-25T16:00:00.000+0000 00168146-ed15-4d18-98b6-d0a65e418035 d1422979-3a3c-42c5-aefc-e0d124452f4c de37844d-425e-47d0-a996-f02d070449ff Gerald Alvarado 379 Deskin Lane Renton WA 99204 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-04 2017-12-20T09:00:00.000+0000 0016ba14-4689-46b6-a781-afbbeb27e8f2 d7a79fe6-fc42-465f-a34f-e665eb25d34f 9ddf6d48-6314-48eb-8107-f98dd3d7bd46 Giana Foley 3 E Whitney Way Westminster CO 81043 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2017.txt 2021-09-17T22:34:20.902+0000 2017-12 2019-01-20T19:00:00.000+0000 002862cc-8e9e-4acf-b505-f219e1309fe0 01efdb4d-3283-471f-81b4-dcc0b68ab187 0522f2e1-4e9e-42ad-a5f9-3df64d3ed9dd Leanna Bradley 525 Wilder Path Orlando FL 32209 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2019.csv 2021-09-17T22:40:33.749+0000 2019-01 2018-07-18T21:00:00.000+0000 002b2d37-8dcf-4fb7-9e97-5f00938206f0 7ad6c8f5-5a5e-4a4f-84ba-0fa7482f6139 a0d447ff-9822-4d4d-bea2-75005cf475b0 Evelynn Erickson 311 Allston Court Davenport IA 51007 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 2018-07 2019-12-28T15:00:00.000+0000 003143e9-ba69-4f86-ab2c-a3f389839a2f d35bf86c-3434-40b6-9eb1-b67729604a9f 37e00f56-7488-473c-af72-5ded2b0f0a20 Crew Simpson 309 Baez Way Detroit MI 48650 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2019.csv 2021-09-17T22:40:33.749+0000 2019-12 2017-10-18T12:00:00.000+0000 003596cf-b0a4-401c-8ed2-9faecc87c4ad eaf2e603-17ab-4c83-9af5-10b60a8d5439 d3ea002f-4199-4aa6-99b9-968f566e75bc Warren Clayton 117 Hibiscus Drive West Jordan UT 84741 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2017.txt 2021-09-17T22:34:20.902+0000 2017-10 2019-02-09T01:00:00.000+0000 003a5cf6-d6b7-4046-9b40-da05b06ccee7 5c8c4151-1757-4a8f-bb17-1fdb71cec041 c20d4f4f-a9b7-41d6-9213-ccad9793a2e3 Stefan Blair 169 Brunell Street Garden Grove CA 94530 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2019.csv 2021-09-17T22:40:33.749+0000 2019-02 2019-11-11T02:00:00.000+0000 003ed0d2-af20-40a6-9751-6fb388282823 e4d4a405-9a5d-41b1-ae87-0eaafd86e267 d7b

In [0]:
df2.write.format("delta").mode("overwrite").partitionBy("submitted_yyyy_mm").saveAsTable(orders_table)

### Reality Check #3.D
Run the following command to ensure that you are on track:

In [0]:
reality_check_03_d()

Points Test Result 
 
 1 
 
 The current database is dbacademy_andrew_barry_infinitive_com_db
 
 
 
 
 1 
 
 The table orders exists
 
 
 
 
 1 
 
 The table orders is a managed table
 
 
 
 
 1 
 
 Using the Delta file format
 
 
 
 
 1 
 
 Schema is valid
 
 
 
 
 1 
 
 Expected 195,698 records
 
 
 
 
 1 
 
 Non-null (properly parsed) submitted_at
 
 
 
 
 1 
 
 Partitioned by submitted_yyyy_mm
 
 
 
 
 1 
 
 Found 36 partitions
 
 
 
 Score: 9

<h2><img src="https://files.training.databricks.com/images/105/logo_spark_tiny.png"> Exercise #3.E - Extract Line Items</h2>

Now that we have extracted sales reps and orders, we next want to extract the specific line items of each order.

**In this step you will need to:**
* Load the table **`batched_orders`** (identified by the variable **`batch_temp_view`**)
* Retain the following columns (see schema below)
  * The correlating ID columns: **`order_id`** and **`product_id`**
  * The two product-specific columns: **`product_quantity`** and **`product_sold_price`**
  * The two ingest columns: **`ingest_file_name`** and **`ingested_at`**
* Convert various columns from their string representation to the specified type:
  * The column **`product_quantity`** should be represented as an **`Integer`**
  * The column **`product_sold_price`** should be represented as an **`Decimal`** with two decimal places as in **`decimal(10,2)`**
* Load the dataset to the managed delta table **`line_items`** (identified by the variable **`line_items_table`**)

**Additional Requirements:**
* The schema for the **`line_items`** table must be:
  * **`order_id`**:**`string`**
  * **`product_id`**:**`string`**
  * **`product_quantity`**:**`integer`**
  * **`product_sold_price`**:**`decimal(10,2)`**
  * **`ingest_file_name`**:**`string`**
  * **`ingested_at`**:**`timestamp`**

### Implement Exercise #3.E

Implement your solution in the following cell:

In [0]:
df3 = spark.sql("select order_id, product_id, product_quantity, product_sold_price, ingest_file_name, ingested_at from batched_orders")
display(df3)

order_id product_id product_quantity product_sold_price ingest_file_name ingested_at c76bccfd-ff08-4aea-8f4e-044f49335d80 7a41323a-560f-4e34-aba6-995e2325f95e 500 101.23 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c76bccfd-ff08-4aea-8f4e-044f49335d80 8d809e13-fdc5-4d15-9271-953750f6d592 700 112.48 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c76bccfd-ff08-4aea-8f4e-044f49335d80 95cbadca-cf90-4b8a-a134-2976f6ba6df8 1000 106.85 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c76bccfd-ff08-4aea-8f4e-044f49335d80 a8fbcfea-4352-4c5a-af8b-c8623258b4f8 1000 111.35 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c76bdbf6-6564-45e5-9393-870c6dec4b27 7b547a10-e804-48e1-ad90-1f946cee659c 900 100.09 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c76bdbf6-6564-45e5-9393-870c6dec4b27 bc93ed89-bb15-4e46-a110-a5878e46ccf6 900 90.08 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 668b2c1f-d76e-4bf0-82bb-c7d5776524a4 500 108.66 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 7a41323a-560f-4e34-aba6-995e2325f95e 800 97.80 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 8d809e13-fdc5-4d15-9271-953750f6d592 600 108.66 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f a990d79b-4957-42fc-8e42-20ceb1fd1259 600 119.53 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f bc93ed89-bb15-4e46-a110-a5878e46ccf6 1000 97.80 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770d7d7-ebed-43ff-9813-6382b02a8500 668b2c1f-d76e-4bf0-82bb-c7d5776524a4 1000 107.71 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770d7d7-ebed-43ff-9813-6382b02a8500 7b547a10-e804-48e1-ad90-1f946cee659c 1000 107.71 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770d7d7-ebed-43ff-9813-6382b02a8500 a8fbcfea-4352-4c5a-af8b-c8623258b4f8 700 106.63 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770d7d7-ebed-43ff-9813-6382b02a8500 ec15ba1d-53b6-44b0-8a22-1e498485f1b8 400 96.94 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c77155ff-a658-4e73-875f-dd849e9e7615 e672483e-57a8-434a-bc42-ecf827c8a8d4 600 104.59 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c77155ff-a658-4e73-875f-dd849e9e7615 ec15ba1d-53b6-44b0-8a22-1e498485f1b8 800 90.08 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c774210c-5395-40d4-8cd3-23a16cbd4728 7a41323a-560f-4e34-aba6-995e2325f95e 700 101.23 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders

In [0]:
df3 = (df3.withColumn("product_quantity", col("product_quantity").astype("int")).withColumn("product_sold_price", col("product_sold_price").astype("decimal(10,2)"))
  .withColumn("ingested_at", to_timestamp(col("ingested_at"))))
  
display(df3)

order_id product_id product_quantity product_sold_price ingest_file_name ingested_at c76bccfd-ff08-4aea-8f4e-044f49335d80 7a41323a-560f-4e34-aba6-995e2325f95e 500 101.23 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c76bccfd-ff08-4aea-8f4e-044f49335d80 8d809e13-fdc5-4d15-9271-953750f6d592 700 112.48 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c76bccfd-ff08-4aea-8f4e-044f49335d80 95cbadca-cf90-4b8a-a134-2976f6ba6df8 1000 106.85 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c76bccfd-ff08-4aea-8f4e-044f49335d80 a8fbcfea-4352-4c5a-af8b-c8623258b4f8 1000 111.35 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c76bdbf6-6564-45e5-9393-870c6dec4b27 7b547a10-e804-48e1-ad90-1f946cee659c 900 100.09 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c76bdbf6-6564-45e5-9393-870c6dec4b27 bc93ed89-bb15-4e46-a110-a5878e46ccf6 900 90.08 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 668b2c1f-d76e-4bf0-82bb-c7d5776524a4 500 108.66 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 7a41323a-560f-4e34-aba6-995e2325f95e 800 97.8 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f 8d809e13-fdc5-4d15-9271-953750f6d592 600 108.66 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f a990d79b-4957-42fc-8e42-20ceb1fd1259 600 119.53 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770a630-5f1e-4b96-b09d-f8b1ec27b25f bc93ed89-bb15-4e46-a110-a5878e46ccf6 1000 97.8 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770d7d7-ebed-43ff-9813-6382b02a8500 668b2c1f-d76e-4bf0-82bb-c7d5776524a4 1000 107.71 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770d7d7-ebed-43ff-9813-6382b02a8500 7b547a10-e804-48e1-ad90-1f946cee659c 1000 107.71 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770d7d7-ebed-43ff-9813-6382b02a8500 a8fbcfea-4352-4c5a-af8b-c8623258b4f8 700 106.63 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c770d7d7-ebed-43ff-9813-6382b02a8500 ec15ba1d-53b6-44b0-8a22-1e498485f1b8 400 96.94 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c77155ff-a658-4e73-875f-dd849e9e7615 e672483e-57a8-434a-bc42-ecf827c8a8d4 600 104.59 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c77155ff-a658-4e73-875f-dd849e9e7615 ec15ba1d-53b6-44b0-8a22-1e498485f1b8 800 90.08 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/batch/2018.csv 2021-09-17T22:37:37.006+0000 c774210c-5395-40d4-8cd3-23a16cbd4728 7a41323a-560f-4e34-aba6-995e2325f95e 700 101.23 dbfs:/user/andrew.barry@infinitive.com/dbacademy/developer-foundations-capstone/raw/orders/b

In [0]:
df3.printSchema()

root
-- order_id: string (nullable = true)
-- product_id: string (nullable = true)
-- product_quantity: integer (nullable = true)
-- product_sold_price: decimal(10,2) (nullable = true)
-- ingest_file_name: string (nullable = true)
-- ingested_at: timestamp (nullable = true)

In [0]:
df3.write.format("delta").mode("overwrite").saveAsTable(line_items_table)

### Reality Check #3.E
Run the following command to ensure that you are on track:

In [0]:
reality_check_03_e()

Points Test Result 
 
 1 
 
 The current database is dbacademy_andrew_barry_infinitive_com_db
 
 
 
 
 1 
 
 The table line_items exists
 
 
 
 
 1 
 
 The table line_items is a managed table
 
 
 
 
 1 
 
 Using the Delta file format
 
 
 
 
 1 
 
 Schema is valid
 
 
 
 
 1 
 
 Expected 1,175,870 records
 
 
 
 Score: 6

<h2><img src="https://files.training.databricks.com/images/105/logo_spark_tiny.png"> Exercise #3 - Final Check</h2>

Run the following command to make sure this exercise is complete:

In [0]:
reality_check_03_final()

Points Test Result 
 
 1 
 
 Reality Check 03.A passed
 
 
 
 
 1 
 
 Reality Check 03.B passed
 
 
 
 
 1 
 
 Reality Check 03.C passed
 
 
 
 
 1 
 
 Reality Check 03.D passed
 
 
 
 
 1 
 
 Reality Check 03.E passed
 
 
 
 Score: 5